# Running Multiple Kriging Tasks

This notebook demonstrates how to run multiple kriging compute tasks concurrently
using the `run_kriging_multiple` function. This is useful for:

- Scenario analysis with different parameters
- Sensitivity studies varying neighborhood settings
- Batch processing multiple attributes

All kriging results are stored as attributes in a single Block Model.

## Authentication

In [1]:
from evo.notebooks import ServiceManagerWidget

manager = await ServiceManagerWidget.with_auth_code(
    client_id="core-compute-tasks-notebooks",  # Replace with your client ID
    base_uri="https://qa-ims.bentley.com",
    discovery_url="https://int-discover.test.api.seequent.com",
    cache_location="./notebook-data",
).login()

ServiceManagerWidget(children=(VBox(children=(HBox(children=(Image(value=b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR…

## Setup for Local Development

> **Note:** If the imports below fail, you may need to add the local source packages to your Python path. Run the cell below first.

In [2]:
# Setup for local development source - run this cell FIRST if you get import errors
# You may need to restart your kernel after running this cell for the first time
import sys

# Remove any cached evo.compute modules to force reimport from local source
mods_to_remove = [key for key in list(sys.modules.keys()) if key.startswith('evo.compute')]
for mod in mods_to_remove:
    del sys.modules[mod]

local_paths = [
    r"C:\Source\evo-python-sdk\packages\evo-compute\src",
    r"C:\Source\evo-python-sdk\packages\evo-blockmodels\src",
    r"C:\Source\evo-python-sdk\packages\evo-objects\src",
    r"C:\Source\evo-python-sdk\packages\evo-sdk-common\src",
]
for path in local_paths:
    if path not in sys.path:
        sys.path.insert(0, path)

print("Local source paths configured - restart kernel if you still see import errors")

Local source paths configured - restart kernel if you still see import errors


## Load Source PointSet and Variogram

Load the source pointset and variogram using `object_from_uuid`.

In [3]:
from evo.objects.typed import object_from_uuid, object_from_path

# Load by UUID (replace with your actual UUIDs)
source_pointset = await object_from_uuid(manager, "9100d7dc-44e9-4e61-b427-159635dea22f")
# Alternative: load by path
# source_pointset = await object_from_path(manager, "path/to/pointset.json")

# Display the pointset (pretty-printed in Jupyter)
source_pointset

In [4]:
# View the pointset attributes
source_pointset.attributes

In [5]:
# Load the variogram
variogram = await object_from_uuid(manager, "72cd9b83-90f4-4cb0-9691-95728e3f9cbb")
# Alternative: load by path
# variogram = await object_from_path(manager, "path/to/variogram.json")

# Display the variogram (pretty-printed in Jupyter)
variogram

In [6]:
# Visualize the variogram - 2D directional curves
from evo.objects.notebooks import plot_variogram

combined, minor, semi_maj, major, ellipsoids = plot_variogram(variogram)
combined.show()

In [7]:
# Individual directional variograms
minor.show()

In [8]:
semi_maj.show()

In [9]:
major.show()

In [10]:
# 3D anisotropy ellipsoids
ellipsoids.show()

In [ ]:
print(f"Source: {source_pointset.name}")
print(f"Variogram: {variogram.name}")

## Create Target Block Model

Create a single Block Model to hold all scenario results as attributes.
The Block Model Service manages concurrent attribute creation.

In [5]:
import uuid
from evo.objects.typed import BlockModel, RegularBlockModelData, Point3, Size3i, Size3d
from evo.blockmodels import Units

run_uuid = uuid.uuid4()

# Create a Block Model to hold all scenario results
# Adjust origin, n_blocks, and block_size to match your data domain
bm_data = RegularBlockModelData(
    name=f"Kriging Scenarios - {run_uuid}",
    description="Block model with kriging results for different max_samples scenarios",
    origin=Point3(x=10000, y=100000, z=200),
    n_blocks=Size3i(nx=40, ny=40, nz=40),
    block_size=Size3d(dx=25.0, dy=25.0, dz=10.0),
    crs="EPSG:32632",
    size_unit_id=Units.METRES,
)

block_model = await BlockModel.create_regular(manager, bm_data)

print(f"Created Block Model: {block_model.name}")
print(f"Block Model UUID: {block_model.block_model_uuid}")
print(f"Bounding Box: {block_model.bounding_box}")

Created Block Model: Kriging Scenarios - 7842b277-7b72-4fd9-a516-282ce98b8062
Block Model UUID: dfde2951-0981-4ed4-bf7e-3f7c221ea2ec
Bounding Box: BoundingBox(min_x=10000.0, min_y=100000.0, max_x=11000.0, max_y=101000.0, min_z=200.0, max_z=600.0)


In [9]:
# Display the block model (pretty-printed in Jupyter)
block_model

## Define Kriging Scenarios

Create multiple parameter sets varying the `max_samples` parameter to study its effect.
All scenarios target the same Block Model, creating different attributes.

In [6]:
from evo.compute.tasks import (
    KrigingParameters,
    Target,
    SearchNeighbourhood,
    Ellipsoid,
    EllipsoidRanges,
    Rotation,
)

# Define different max_samples values to test
max_samples_values = [5, 10, 15, 20]

# Search ellipsoid configuration
search_ellipsoid = Ellipsoid(
    ranges=EllipsoidRanges(major=200.0, semi_major=150.0, minor=100.0),
    rotation=Rotation(dip_azimuth=0.0, dip=0.0, pitch=0.0),
)

# Base source configuration
source = source_pointset.attributes["Ag_ppm Values"]

# Create parameter sets for each scenario, all targeting the same Block Model
# Note: method defaults to ordinary kriging, so we don't need to specify it
parameter_sets = []
for max_samples in max_samples_values:
    params = KrigingParameters(
        source=source,
        target=Target.new_attribute(block_model, attribute_name=f"Samples={max_samples}"),
        variogram=variogram,
        search=SearchNeighbourhood(ellipsoid=search_ellipsoid, max_samples=max_samples),
    )
    parameter_sets.append(params)
    print(f"Prepared scenario with max_samples={max_samples}")

print(f"\nCreated {len(parameter_sets)} parameter sets")

Prepared scenario with max_samples=5
Prepared scenario with max_samples=10
Prepared scenario with max_samples=15
Prepared scenario with max_samples=20

Created 4 parameter sets


## Run Multiple Kriging Tasks

Execute all scenarios concurrently using `run_kriging_multiple`.
Progress is aggregated across all tasks.

In [7]:
from evo.compute.tasks import run_kriging_multiple
from evo.notebooks import FeedbackWidget

# Run all scenarios in parallel
print(f"Submitting {len(parameter_sets)} kriging tasks in parallel...")
fb = FeedbackWidget("Kriging Scenarios")

results = await run_kriging_multiple(manager, parameter_sets, fb=fb)

print(f"\nAll {len(results)} scenarios completed!")

Submitting 4 kriging tasks in parallel...



All 4 scenarios completed!


## View Block Model Attributes

Display the block model attributes to see all the newly created scenario columns.

> **Note:** The block model object needs to be refreshed to see the newly added attributes.

In [8]:
# Refresh the block model to see the new attributes added by kriging
block_model = await block_model.refresh()

# Pretty-print the block model to see its current state
block_model

In [9]:
# View just the attributes (pretty-printed table in Jupyter)
block_model.attributes

BlockModelAttributes(['version_id', 'Samples=5', 'Samples=10', 'Samples=15', 'Samples=20'])

## Query Results from Block Model

Get all scenario results from the Block Model.

In [10]:
# Query the Block Model for all scenario columns using to_dataframe()
scenario_columns = [f"Samples={ms}" for ms in max_samples_values]

print("Querying Block Model for results...")
df = await block_model.to_dataframe(columns=scenario_columns)

print(f"Retrieved {len(df)} blocks with {len(scenario_columns)} scenario columns")
df.head(10)

Querying Block Model for results...
Retrieved 64000 blocks with 4 scenario columns


x         y      z  Samples=5  Samples=10  Samples=15  Samples=20
0  10662.5  100012.5  405.0        NaN         NaN         NaN         NaN
1  10662.5  100012.5  415.0        NaN         NaN         NaN         NaN
2  10662.5  100012.5  425.0        NaN         NaN         NaN         NaN
3  10662.5  100012.5  435.0        NaN         NaN         NaN         NaN
4  10662.5  100012.5  445.0        NaN         NaN         NaN         NaN
5  10662.5  100012.5  455.0        NaN         NaN         NaN         NaN
6  10662.5  100012.5  465.0        NaN         NaN         NaN         NaN
7  10662.5  100012.5  475.0        NaN         NaN         NaN         NaN
8  10662.5  100012.5  485.0        NaN         NaN         NaN         NaN
9  10662.5  100012.5  495.0        NaN         NaN         NaN         NaN

## Display Results

In [22]:
# Pretty-print the Block Model with all scenarios (includes Portal/Viewer links)
block_model

In [23]:
# Show individual job result messages
for i, (job_result, max_samples) in enumerate(zip(results, max_samples_values)):
    print(f"Scenario {i+1}: max_samples={max_samples} - {job_result.message}")

Scenario 1: max_samples=5 - Kriging completed.
Scenario 2: max_samples=10 - Kriging completed.
Scenario 3: max_samples=15 - Kriging completed.
Scenario 4: max_samples=20 - Kriging completed.


In [24]:
# Display first result (pretty-printed)
results[0]

✓ Kriging Result
  Message:   Kriging completed.
  Target:    Kriging Scenarios - 7adfc634-f4b3-47ec-84e4-a829bde8d343
  Attribute: Samples=5

## Analyze Results

Compare the kriging results across different max_samples values.

In [25]:
# Show statistics for each scenario
print("Statistics by max_samples:")
print(df[scenario_columns].describe())

Statistics by max_samples:
          Samples=5    Samples=10    Samples=15    Samples=20
count  10649.000000  10649.000000  10649.000000  10649.000000
mean     112.093617    111.122638    111.041452    110.780011
std       70.023416     64.705758     61.856261     59.592869
min        6.887604      8.570578     11.116600     11.116600
25%       57.448091     62.219550     64.765351     67.859388
50%      102.442995    103.043904    102.803484    102.203295
75%      141.242807    137.407133    136.124138    136.126375
max      677.854549    685.066753    538.751039    479.741686


In [26]:
# Optional: Visualize the differences using plotly
try:
    import plotly.express as px

    # Melt the data for box plot comparison
    df_melted = df[scenario_columns].melt(var_name="Scenario", value_name="value")

    fig = px.box(
        df_melted,
        x="Scenario",
        y="value",
        title="Kriging Values by Max Samples",
    )
    fig.show()
except ImportError:
    print("Install plotly for visualization: pip install plotly")
